In [3]:
import geopandas as gpd
import pandas as pd
from bisonlab.data import LOCAL_DATA_DIR, DATA_DIR
from bisonlab.io import kml_to_geodataframe, kmz_to_geodataframe

In [4]:
#
filepath = LOCAL_DATA_DIR / "morton_plots.kml"
df_morton_plots = kml_to_geodataframe(filepath)

df_morton_plots.drop(columns=["Description", "layer"], inplace=True)
df_morton_plots.rename(columns={"Name": "name"}, inplace=True)

df_morton_plots = df_morton_plots.to_crs(crs=crs)

DriverError: /Users/chill/software/bison-lab/data/local/morton_plots.kml: No such file or directory

# SSURGO

In [5]:
ls /Users/chill/Downloads/wss_aoi_2023-03-01_17-16-33/tabular

ccancov.txt             cinterp.txt             legend.txt
ccrpyd.txt              cmonth.txt              ltext.txt
cdfeat.txt              comp.txt                mapunit.txt
cecoclas.txt            cpmat.txt               msdomdet.txt
ceplants.txt            cpmatgrp.txt            msdommas.txt
cerosnac.txt            cpwndbrk.txt            msidxdet.txt
cfprod.txt              crstrcts.txt            msidxmas.txt
cfprodo.txt             csfrags.txt             msrsdet.txt
cgeomord.txt            csmoist.txt             msrsmas.txt
chaashto.txt            csmorgc.txt             mstab.txt
chconsis.txt            csmorhpp.txt            mstabcol.txt
chdsuffx.txt            csmormr.txt             muaggatt.txt
chfrags.txt             csmorss.txt             muareao.txt
chorizon.txt            cstemp.txt              mucrpyd.txt
chpores.txt             ctext.txt               mutext.txt
chstr.txt               ctreestm.txt            sacatlog.txt
chstrgrp.txt            ctxfmmin.txt   

In [10]:
ssurgo_musym

desc
MUSYM                                                   
GrA                   Griffy loam, 0 to 3 percent slopes
GrB                   Griffy loam, 3 to 6 percent slopes
GrC                  Griffy loam, 6 to 10 percent slopes
Gu                                          Gullied land
LoA     Lostwells sandy clay loam, 0 to 3 percent slopes
...                                                  ...
001    Effington-Binton silty clay loams, 0 to 6 perc...
408           Trook-Apron complex, 0 to 6 percent slopes
ApB              Apron sandy loam, 2 to 6 percent slopes
Cw     Crowheart loam, 0 to 3 percent slopes, occasio...
Bg     Bigwin fine sandy loam, 0 to 2 percent slopes,...

[101 rows x 1 columns]

In [6]:
ssurgo_mu = gpd.read_file("/Users/chill/Downloads/wss_aoi_2023-03-01_17-16-33/spatial/soilmu_a_aoi.shp")
ssurgo_musym = pd.read_csv("/Users/chill/Downloads/wss_aoi_2023-03-01_17-16-33/tabular/muaggatt.txt", delimiter='|', header=None)
ssurgo_musym = ssurgo_musym[[0, 1]].rename(columns={0: 'MUSYM', 1: 'desc'})
ssurgo_musym = ssurgo_musym.drop_duplicates(subset="MUSYM", keep="last").set_index('MUSYM')
ssurgo = ssurgo_mu.join(ssurgo_musym, on='MUSYM')
ssurgo['MUKEY'] = ssurgo['MUKEY'].astype(int)

In [65]:
ssurgo.to_parquet(LOCAL_DATA_DIR.parent / "soil_taxonomy.parquet") 

In [9]:
ssurgo.to_file(LOCAL_DATA_DIR.parent / "soil_ssurgo.shp", index=False) 

In [66]:
ssurgo = gpd.read_parquet(LOCAL_DATA_DIR.parent / "soil_taxonomy.parquet") 

# Parcels

In [4]:
# local_data = Path().cwd().parent.parent / "data" / "local"
# df_parcels = kml_to_geodataframe(local_data / "WRTBI-Morton Soil Types.kml")
# df_parcels = df_parcels.rename(columns={"Name": "subsection", "layer": "parcel"})
# df_parcels = df_parcels.drop(columns="Description")

# # Union all "mask" polygons and create a separate mask dataframe
# idx = df_parcels["parcel"] == "mask"
# df_mask = df_parcels[idx].dissolve(by="parcel").reset_index()

# # Drop "mask" from parcel dataframe
# df_parcels = df_parcels.drop(index=idx.index[idx])
# df_parcels['label'] = df_parcels['parcel'] + " - " + df_parcels['subsection']

# # Convert parcels dataframe to ee.featureCollection
# parcels = geemap.geopandas_to_ee(df_parcels)
# mask = geemap.geopandas_to_ee(df_mask)

/Users/chill/software/miniconda3/envs/bison-lab/lib/python3.10/site-packages/geopandas/io/file.py:545: UserWarning: You are attempting to write an empty DataFrame to file. For some drivers, this operation may fail.
  _to_file_fiona(df, filename, driver, schema, crs, mode, **kwargs)


In [52]:
# list(df_parcels['label'])

# Intersect soil and slope with parcels
* We want only regions with `slope < 10 deg`, intersected with parcel boundaries and soil boundaries

In [40]:
# Mask for slope
slope_mask = slope.lt(10)

In [41]:
# # Apply slope mask to soil taxonomy

# # First rasterize soil map
# soil_taxonomy_img = soil_taxonomy.reduceToImage(
#     properties=['soil_id'],
#     reducer=ee.Reducer.first()
# ).rename("soil_id")

# # Then apply slope mask
# soil_taxonomy_img = soil_taxonomy_img.updateMask(slope_mask)

In [25]:
# # Get area of soil type per parcel
# parcel_soil_area = soil_taxonomy_img.reduceRegions(
#     collection=parcels, reducer=ee.Reducer.frequencyHistogram(), scale=1 # 1m scale = 1 m^2 pixels
# )

# df = geemap.ee_to_df(parcel_soil_area.select(["histogram", "name"]))

# soil_per_parcel = pd.concat([
#     pd.DataFrame(data=row["histogram"].values(), index=row["histogram"].keys(), columns=[row["name"]])
#     for i, row in df.iterrows()
# ], axis=1)

In [26]:
# soil_per_parcel.round(1)

In [27]:
# soil_per_parcel.plot.bar(figsize=(12, 6), ylabel="area_m2");

In [42]:
# # vectorize slope mask
# slope_mask_vectors = slope_mask.reduceToVectors(
#     geometry=parcel_bounds,
#     crs=slope_mask.projection(),
#     scale=5,
#     geometryType='polygon',
#     eightConnected=False,
#     maxPixels=1e13,
#     labelProperty='slope',
# )
# # Make single polygon
# slope_vector = slope_mask_vectors.filterMetadata("slope", "greater_than", 0).geometry().dissolve(1)

In [43]:
# m = geemap.Map()
# m.addLayer(slope_vector, {}, 'Slope')
# m.addLayer(parcels_styled, {}, "Parcels")
# m.centerObject(parcels, 14)
# m

In [44]:
# slope_shapely = shapely.geometry.shape(slope_vector.getInfo())

In [45]:
# slope = gpd.GeoSeries(slope_shapely, crs=crs)

## Intersect polygons for parcels and the given soil type(s)

In [48]:
# intersect parcels and soil
df_soil_taxonomy['soil_geom'] = df_soil_taxonomy.geometry
df_intersect = gpd.sjoin(left_df=df_parcels, right_df=df_soil_taxonomy, how="inner", predicate="intersects").reset_index(drop=True)

In [49]:
df_intersect.name.unique()

array(['Shoshone Tribe', 'Hellyer Tribal Lease', 'Buffalo Initiative',
       'Hellyer Place', 'Hoopengarner Property', 'Wickstram Property'],
      dtype=object)

### Soil Per Parcel

In [102]:
# Calc area of overlap between soil and parcels

soil_taxonomy_intersection = (
    df_intersect['geometry'].buffer(0)
    .intersection(
        df_intersect['soil_geom'].buffer(0)
    )
)

df_intersect['area_overlap_m2'] = soil_taxonomy_intersection.area

# Soils per parcel
soil_per_parcel = df_intersect.groupby("name").apply(lambda g: g.sort_values("area_overlap_m2", ascending=False)).reset_index(level=1, drop=True)
soil_per_parcel = soil_per_parcel.drop(columns=["index_right", "SPATIALVER", "SPATIALVER", "AREASYMBOL", "name"]).reset_index(drop=False)

In [104]:
# soil_per_parcel

### Parcel per soil

In [105]:
# Parcels per soil
parcel_per_soil = df_intersect.groupby("MUSYM").apply(lambda g: g.sort_values("area_overlap_m2", ascending=False)).reset_index(level=1, drop=True)
parcel_per_soil = parcel_per_soil.drop(columns=["index_right", "SPATIALVER", "SPATIALVER", "AREASYMBOL", "MUSYM"]).reset_index(drop=False)
parcel_per_soil['area_overlap_hectare'] = parcel_per_soil['area_overlap_m2'] / 10_000

In [106]:
# parcel_per_soil

### Apply slope mask

In [528]:
# soil_per_parcel.query("name == 'Shoshone Tribe' and MUSYM == 'EtA'").iloc[0].geometry.intersection(
    # slope.geometry)

In [98]:
slope.geometry.intersection(soil_per_parcel.iloc[0].geometry)

0    POLYGON EMPTY
dtype: geometry

In [68]:
polys = []
for i, row in soil_per_parcel.iterrows():
    polys.append(slope.intersection(row.geometry).intersection(row.soil_geom))

soil_per_parcel["geometry_parcel_soil_slope"] = polys

In [69]:
soil_per_parcel.loc[
    ["Shoshone Tribe", "Hellyer Tribal Lease", "Hellyer Place"], :
]

geometry  \
name                                                                      
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Shoshone Tribe        POLYGON ((-1030780.069 2315216.076, -1031458.9...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Tribal Lease  POLYGON ((-1031801.689 2314930.485, -1032203.5...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   
Hellyer Place         POLYGON ((-1031247.137 2316088.631, -1031631.6...   

                      parcel_id  MUSYM   MUKEY  \
name                                             
Shoshone Tribe                1    GrA  157364   
Shoshone Tribe                1    EtA  157353   
Shoshone Tribe                1    CRF  157345   
Shoshone Tribe                1    CRF  157345   
Shoshone Tribe                1     Bn  157341   
Shoshone Tribe                1     Cw  157347   
Shoshone Tribe                1     Cw  157347   
Shoshone Tribe                1    EtA  157353   
Shoshone Tribe                1     Wa  157405   
Shoshone Tribe                1     Bg  157339   
Shoshone Tribe                1    EtB  157354   
Hellyer Tribal Lease          6     Bn  157341   
Hellyer Tribal Lease          6     Cw  157347   
Hellyer Tribal Lease          6    CRF  157345   
Hellyer Tribal Lease          6     Wa  157405   
Hellyer Tribal Lease          6    EtA  157353   
Hellyer Tribal Lease          6     Cw  157347   
Hellyer Tribal Lease          6     Bg  157339   
Hellyer Tribal Lease          6  ZZ900  157414   
Hellyer Tribal Lease          6    GrA  157364   
Hellyer Place                 3    EtA  157353   
Hellyer Place                 3    EtA  157353   
Hellyer Place                 3    EuB  157355   
Hellyer Place                 3    CRF  157345   
Hellyer Place                 3     Cw  157347   
Hellyer Place                 3    CRF  157345   
Hellyer Place                 3    Pa

In [608]:
ee_final = geemap.geopandas_to_ee(soil_per_parcel)

TypeError: Cannot interpret '<geopandas.array.GeometryDtype object at 0x15f96a920>' as a data type

In [348]:
parcels_first = ee.Feature(parcels.first())

In [352]:
spatial_filter = ee.Filter.intersects(
  leftField='.geo',
  rightField='.geo',
  maxError=1
)
save_all_join = ee.Join.saveAll(
  matchesKey='soil_id'
)
intersect_joined = save_all_join.apply(parcels, soil_taxonomy, spatial_filter)

In [ ]:
save_all_join = ee.Join.saveAll(
  matchesKey='soil_id'
)
intersect_joined = save_all_join.apply(parcels, soil_taxonomy, spatial_filter)

In [353]:
df = geemap.ee_to_df(intersect_joined)

In [406]:
# df.soil_id[0]

In [276]:
intersect_joined.select('MUKEY')

In [ ]:
<10 deg slope
soil type
jason's parcels

In [16]:
# m = geemap.Map()
# m.addLayer(terrain.select('slope'), {min: 0, max: 89.99}, 'Slope')
# m.addLayer(terrain.select('aspect'), {min: 0, max: 359.99}, 'Aspect')
# m.addLayer(terrain.select('hillshade'), {min: 0, max: 255}, 'Hillshade')
# m.centerObject(parcels, 11)
# m

In [55]:
dem_min = dem.reduceRegions(bounds, ee.Reducer.min(), scale=30)

In [61]:
dem_min.first()

In [62]:
dem_max = dem.reduceRegions(bounds, ee.Reducer.max(), scale=30)

In [63]:
dem_max

In [31]:
parcels

In [48]:
parcel_labels = list(df_parcels.label)
parcel_colors = [f"{random.randint(0, 0xFFFFFF):06x}" for i in range(len(df_parcels))]
parcels_styled = geemap.ee_vector_style(
    parcels, column='label', labels=parcel_labels,
    fillColor='00000000', color=parcel_colors, width=5
)

In [45]:
keys = list(ssurgo['MUSYM'].unique())
colors = [f"{random.randint(0, 0xFFFFFF):06x}" for i in range(len(keys))]
styled_fc = geemap.ee_vector_style(
    ee_ssurgo, column='MUSYM', labels=keys, fillColor=colors, color='00000000'
)

In [39]:
lgrip30 = ee.ImageCollection("projects/sat-io/open-datasets/GFSAD/LGRIP30")
irr_colors = ["0050cb","d58855","c2d30c","379a4b"]
irr_labels = ["Ocean", "Non-croplands", "Irrigated croplands", "Rainfed croplands"]
vis = {"min":0,"max":3,"palette":irr_colors}

In [52]:
m = geemap.Map()
m.addLayer(styled_fc, {}, 'MUSYM')
m.addLayer(terrain.select('slope'), {min: 0, max: 5}, 'Slope')
m.addLayer(terrain.select('aspect'), {min: 0, max: 359.99}, 'Aspect')
m.addLayer(terrain.select('hillshade'), {min: 0, max: 255}, 'Hillshade')
m.addLayer(lgrip30.mosaic(), vis, 'Irrigated')
m.addLayer(parcels_styled, {}, "Parcels")

m.add_legend(title='irr', labels=irr_labels, colors=irr_colors, position="topleft")
m.add_legend(title='MUSYM', labels=keys, colors=colors, position="bottomright")
m.add_legend(title='parcels', labels=parcel_labels, colors=parcel_colors, position="bottomleft")
m.centerObject(parcels, 11)
# m.centerObject(fc, 12)
m

KeyboardInterrupt: 

In [ ]:
<10 deg slope
soil type
jason's parcels

## Join Parcels and SSURGO

In [7]:
ssurgo['ssurgo_geom'] = ssurgo.geometry
intersects = gpd.sjoin(left_df=df_parcels, right_df=ssurgo, how="inner", predicate="intersects").reset_index(drop=True)

In [8]:
crs = "ESRI:102008"

In [9]:
ssurgo_intersection = (
    intersects['geometry'].buffer(0).to_crs(crs)
    .intersection(
        intersects['ssurgo_geom'].buffer(0).to_crs(crs))
    )
ssurgo_intersection = ssurgo_intersection.to_crs(crs)
intersects['area_overlap_m2'] = ssurgo_intersection.area

/Users/chill/software/miniconda3/envs/bison-lab/lib/python3.10/site-packages/shapely/constructive.py:181: RuntimeWarning: invalid value encountered in buffer
  return lib.buffer(
/Users/chill/software/miniconda3/envs/bison-lab/lib/python3.10/site-packages/shapely/set_operations.py:133: RuntimeWarning: invalid value encountered in intersection
  return lib.intersection(a, b, **kwargs)


In [10]:
# Soils per parcel
soil_per_parcel = intersects.groupby("label").apply(lambda g: g.sort_values("area_overlap_m2", ascending=False)).reset_index(level=1, drop=True)

In [16]:
# soil_per_parcel

In [17]:
# soil_per_parcel.loc["Shoshone Tribe - High Steppe Unirrigated 1"]
# [["MUSYM", "desc", "area_overlap_m2"]]

In [18]:
# Parcels per soil
parcel_per_soil = intersects.groupby("MUSYM").apply(lambda g: g.sort_values("area_overlap_m2", ascending=False)).reset_index(level=1, drop=True)

In [24]:
parcel_per_soil['area_overlap_hectare'] = parcel_per_soil['area_overlap_m2'] / 10_000

In [25]:
# parcel_per_soil#[["label", "geometry", "MUSYM", "desc", "ssurgo_geom", "area_overlap_m2"]]

In [26]:
# parcel_per_soil

In [27]:
# parcel_per_soil.loc[parcel_per_soil['parcel'].isin([
#     'Shoshone Tribe',
#     'Morton',
#     'Hellyer Tribal Lease',
#     'Business as Usual - Business as Usual'
#     ]),
#     ["parcel", "label", "area_overlap_hectare", "desc"]].reset_index().set_index(["MUSYM", "label"]).round(1)#.to_csv('parcels_per_soil.csv')

In [28]:
# parcel_per_soil[["parcel", "label", "area_overlap_hectare", "desc"]].reset_index().set_index(["MUSYM", "label"]).round(1)#.to_csv('parcels_per_soil.csv')

In [33]:
parcel_per_soil.loc["CRF", ["parcel", "label", "area_overlap_hectare", "desc"]].round(1)

parcel                                       label  \
MUSYM                                                                     
CRF          Shoshone Tribe  Shoshone Tribe - High Steppe Unirrigated 1   
CRF               Untouched        Untouched - Untouched 1: High Steppe   
CRF          Shoshone Tribe             Shoshone Tribe - River Bottom 2   
CRF                  Morton            Morton - Irrigated High Steppe 2   
CRF    Hellyer Tribal Lease       Hellyer Tribal Lease - River Bottom 1   
CRF                  Morton            Morton - Irrigated High Steppe 1   
CRF          Shoshone Tribe  Shoshone Tribe - High Steppe Unirrigated 4   
CRF          Shoshone Tribe             Shoshone Tribe - River Bottom 1   
CRF          Shoshone Tribe             Shoshone Tribe - River Bottom 3   
CRF          Shoshone Tribe             Shoshone Tribe - River Bottom 3   

       area_overlap_hectare                                     desc  
MUSYM                                                                 
CRF                     7.3  Clifterson-Rock land association, steep  
CRF                     3.8  Clifterson-Rock land association, steep  
CRF                     2.4  Clifterson-Rock land association, steep  
CRF                     1.8  Clifterson-Rock land association, steep  
CRF                     1.2  Clifterson-Rock land association, steep  
CRF                     0.7  Clifterson-Rock land association, steep  
CRF                     0.6  Clifterson-Rock land association, steep  
CRF                     0.2  Clifterson-Rock land association, steep  
CRF                     0.2  Clifterson-Rock land association, steep  
CRF                     0.0  Clifterson-Rock land association, steep

In [123]:
# intersects.groupby("label").aggregate(intersects[["MUSYM", "area_overlap_m2"]])

In [58]:
fc = geemap.geopandas_to_ee(df)

In [90]:
import random

In [91]:
keys = list(df['MUSYM'].unique())
colors = [f"{random.randint(0, 0xFFFFFF):06x}" for i in range(len(keys))]
styled_fc = geemap.ee_vector_style(
    fc, column='MUSYM', labels=keys, fillColor=colors, color='00000000'
)

In [135]:
df_plot = df_parcels.loc[df_parcels['label'].isin([
'Shoshone Tribe - High Steppe Unirrigated 1',
 'Shoshone Tribe - High Steppe Unirrigated 2',
 'Shoshone Tribe - High Steppe Unirrigated 3',
 'Shoshone Tribe - High Steppe Unirrigated 4',
 'Shoshone Tribe - River Bottom 1',
 'Shoshone Tribe - River Bottom 2',
 'Shoshone Tribe - River Bottom 3',
    'Hellyer Tribal Lease - River Bottom 1',
     'Business as Usual - Business as Usual'
        ]), :]
parcel_labels = list(df_plot['label'])
# parcel_labels = list(df_parcels['label'])

parcel_colors = [f"{random.randint(0, 0xFFFFFF):06x}" for i in range(len(parcel_labels))]
parcels_styled = geemap.ee_vector_style(
    parcels, column='label', labels=parcel_labels,
    # fillColor=parcel_colors, color='00000000'
    fillColor='00000000', color=parcel_colors, width=5
)

In [155]:
m = geemap.Map()

m.addLayer(styled_fc, {}, 'MUSYM')


m.addLayer(lgrip30.mosaic(), vis, 'LGRIP30')
m.addLayer(parcels_styled, {}, "Parcels")

m.add_legend(title='irr', labels=irr_labels, colors=irr_colors, position="topleft")
m.add_legend(title='MUSYM', labels=keys, colors=colors, position="bottomright")
m.add_legend(title='parcels', labels=parcel_labels, colors=parcel_colors, position="bottomleft")

m.centerObject(fc, 12)
m

Map(center=[43.20731467345074, -108.8565111395239], controls=(WidgetControl(options=['position', 'transparent_…